In [1]:
import sqlite3
from smolagents import CodeAgent, DuckDuckGoSearchTool, LiteLLMModel
from dotenv import load_dotenv
import os
import json

load_dotenv()
cohere_token = os.getenv("cohere_key")

# Define the agent
model = LiteLLMModel(
    model_id="command-r",
    api_key=cohere_token,
)
agent = CodeAgent(tools=[DuckDuckGoSearchTool()], model=model)

# Define the function to choose the best algorithm
def choose_best_algorithm(train_db_file="train_mTSP.sqlite3", test_db_file="test_mTSP.sqlite3"):

    conn_train = sqlite3.connect(train_db_file)
    cursor_train = conn_train.cursor()

    # Select instances from the training database
    cursor_train.execute("""
        SELECT instance_id, nr_cities, nr_salesmen, average_distance, stddev_distance, density, salesmen_ratio, 
               bounding_box_area, aspect_ratio, spread, cluster_compactness, mst_total_length, entropy_distance_matrix 
        FROM instances 
    """)
    train_instances = cursor_train.fetchall()
    train_instances_with_columns = [
        {
            "instance_id": row[0], 
            "nr_cities": row[1], 
            "nr_salesmen": row[2],
            "average_distance": row[3],
            "stddev_distance": row[4],
            "density": row[5],
            "salesmen_ratio": row[6],
            "bounding_box_area": row[7],
            "aspect_ratio": row[8],
            "spread": row[9],
            "cluster_compactness": row[10],
            "mst_total_length": row[11],
            "entropy_distance_matrix": row[12]
        } for row in train_instances
    ]

    # Select algorithms from the training database
    cursor_train.execute("""
        SELECT instance_id, strategy, total_cost, normalized_cost, time_taken, distance_gap, efficiency 
        FROM algorithms 
        WHERE instance_id IN (SELECT instance_id FROM instances)
    """)
    train_algorithms_data = cursor_train.fetchall()
    train_algorithms_with_columns = [
        {
            "instance_id": row[0],
            "strategy": row[1],
            "total_cost": row[2],
            "normalized_cost": row[3],
            "time_taken": row[4],
            "distance_gap": row[5],
            "efficiency": row[6],
        }
        for row in train_algorithms_data
    ]


    conn_train.close()
    conn_test = sqlite3.connect(test_db_file)
    cursor_test = conn_test.cursor()

    # Select instances from the test database
    cursor_test.execute("""
        SELECT instance_id, nr_cities, nr_salesmen, average_distance, stddev_distance, density, salesmen_ratio, 
               bounding_box_area, aspect_ratio, spread, cluster_compactness, mst_total_length, entropy_distance_matrix 
        FROM instances 
    """)
    test_instances = cursor_test.fetchall()
    test_instances_with_columns = [
        {
            "instance_id": row[0], 
            "nr_cities": row[1], 
            "nr_salesmen": row[2],
            "average_distance": row[3],
            "stddev_distance": row[4],
            "density": row[5],
            "salesmen_ratio": row[6],
            "bounding_box_area": row[7],
            "aspect_ratio": row[8],
            "spread": row[9],
            "cluster_compactness": row[10],
            "mst_total_length": row[11],
            "entropy_distance_matrix": row[12]
        } for row in test_instances
    ]

    conn_test.close()

    # Prepare the data for the agent
    data = {
        "train_instances": train_instances_with_columns,
        "train_algorithms": train_algorithms_with_columns,
        "test_instances": test_instances_with_columns,
    }
    data_str = json.dumps(data, indent=4)

    # Task for the agent
    task = f"""
    You are an AI agent tasked with selecting the best algorithm for solving each instance of the mTSP problem.
    Below is the data from the training instances and their results for different strategies:

    {data_str}

    Your task is to:
    1. Analyze the performance of each strategy (Greedy, Branch and Cut, Ant Colony, KMeans-Greedy) on the training instances.
    2. Based on this analysis, recommend the best strategy for each test instance.
    3. Justify your recommendations based on the training data.
    4. Consider the following performance metrics: total cost, normalized_cost, time taken, efficiency, and distance gap. The total cost is the most important metric, followed by normalized_cost and efficiency. Time taken is less important, but it should be considered for strategies that are computationally expensive.
    5. Take into account that Branch and Cut and Ant Colony are more computationally expensive, while Greedy and KMeans-Greedy are faster but may not always yield the best results.
    6. Branch and Cut and Ant Colony have a 100 seconds time limit, so they may output a weaker solution if the time limit is reached or even no solution at all.

    Output your recommendations in the following format:
    [
    {{ "instance_id": <test_instance_id>, "recommended_strategy": <strategy>, "justification": <reason> }}
    ]   
    """

    response = agent.run(task)
    print(response)

choose_best_algorithm(train_db_file="train_mTSP.sqlite3", test_db_file="test_mTSP.sqlite3")


c:\Users\ignat\AppData\Local\Programs\Python\Python312\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


╭──────────────────────────────────────────────────── New run ────────────────────────────────────────────────────╮
│                                                                                                                 │
│ You are an AI agent tasked with selecting the best algorithm for solving each instance of the mTSP problem.     │
│     Below is the data from the training instances and their results for different strategies:                   │
│                                                                                                                 │
│     {                                                                                                           │
│     "train_instances": [                                                                                        │
│         {                                                                                                       │
│             "instance_id": 1,                                                                                   │
│             "nr_cities": 15,                                                                                    │
│             "nr_salesmen": 3,                                                                                   │
│             "average_distance": 56.8570887516831,                                                               │
│             "stddev_distance": 25.10620358961564,                                                               │
│             "density": 0.0064376232735148435,                                                                   │
│             "salesmen_ratio": 0.2,                                                                              │
│             "bounding_box_area": 8832.0,                                                                        │
│             "aspect_ratio": 0.9583333333333334,                                                                 │
│             "spread": 1.9711070030059819,                                                                       │
│             "cluster_compactness": 3.79047258344554,                                                            │
│             "mst_total_length": 309.276067867573,                                                               │
│             "entropy_distance_matrix": 2.7959530609379706                                                       │
│         },                                                                                                      │
│         {                                                                                                       │
│             "instance_id": 2,                                                                                   │
│             "nr_cities": 15,                                                                                    │
│             "nr_salesmen": 3,                                                                                   │
│             "average_distance": 57.185738976704414,                                                             │
│             "stddev_distance": 26.83482670625802,                                                               │
│             "density": 0.0066125970139574945,                                                                   │
│             "salesmen_ratio": 0.2,                                                                              │
│             "bounding_box_area": 8648.0,                                                                        │
│             "aspect_ratio": 1.0217391304347827,                                                                 │
│             "spread": 2.239754303662321,                                                                        │
│             "cluster_compactness": 3.812382598446961,                                                           │
│             "mst_total_length": 310.72208166143344,   

━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ Step 1 ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

Error in code parsing:
Your code snippet is invalid, because the regex pattern ```(?:py|python)?\n(.*?)\n``` was not found in it.
            Here is your code snippet:
            To recommend the best strategy for each test instance, I'll analyze the performance of each strategy on
the training instances based on the provided metrics. Here's a summary of the analysis:

1. **Branch and Cut**: 
   - Generally has the lowest total cost and normalized cost, indicating it finds the best solutions.
   - However, it's computationally expensive, with time taken often exceeding 0.1 seconds, and in some cases, 
reaching the 100-second limit.
   - Efficiency is high, but it may not complete within the time limit for larger instances.

2. **Ant Colony**:
   - Total cost and normalized cost are higher than Branch and Cut but still competitive.
   - Computationally expensive, with time taken often exceeding 0.4 seconds, and may reach the 100-second limit.
   - Efficiency is moderate, but it can find good solutions for smaller instances.

3. **Greedy**:
   - Total cost and normalized cost are higher than Branch and Cut and Ant Colony.
   - Extremely fast, with time taken close to 0 seconds.
   - Efficiency is high due to its speed, but solution quality is lower.

4. **KMeans-Greedy**:
   - Total cost and normalized cost are similar to Greedy, but slightly worse.
   - Also very fast, with time taken close to 0 seconds.
   - Efficiency is high, but solution quality is lower than Greedy.

Based on this analysis, here are the recommendations for each test instance:

```json
[
    {
        "instance_id": 1,
        "recommended_strategy": "Branch and Cut",
        "justification": "Small instance with 10 cities, Branch and Cut can find the optimal solution within the 
time limit."
    },
    {
        "instance_id": 2,
        "recommended_strategy": "Branch and Cut",
        "justification": "Small instance with 10 cities, Branch and Cut can find the optimal solution within the 
time limit."
    },
    {
        "instance_id": 3,
        "recommended_strategy": "Branch and Cut",
        "justification": "Small instance with 10 cities, Branch and Cut can find the optimal solution within the 
time limit."
    },
    {
        "instance_id": 4,
        "recommended_strategy": "Branch and Cut",
        "justification": "Small instance with 10 cities, Branch and Cut can find the optimal solution within the 
time limit."
    },
    {
        "instance_id": 5,
        "recommended_strategy": "Branch and Cut",
        "justification": "Small instance with 10 cities, Branch and Cut can find the optimal solution within the 
time limit."
    },
    {
        "instance_id": 6,
        "recommended_strategy": "Branch and Cut",
        "justification": "Small instance with 10 cities, Branch and Cut can find the optimal solution within the 
time limit."
    },
    {
        "instance_id": 7,
        "recommended_strategy": "Branch and Cut",
        "justification": "Small instance with 10 cities, Branch and Cut can find the optimal solution within the 
time limit."
    },
    {
        "instance_id": 8,
        "recommended_strategy": "Branch and Cut",
        "justification": "Small instance with 10 cities, Branch and Cut can find the optimal solution within the 
time limit."
    },
    {
        "instance_id": 9,
        "recommended_strategy": "Branch and Cut",
        "justification": "Small instance with 10 cities, Branch and Cut can find the optimal solution within the 
time limit."
    },
    {
        "instance_id": 10,
        "recommended_strategy": "Branch and Cut",
        "justification": "Small instance with 10 cities, Branch and Cut can find the optimal solution within the 
time limit."
    },
    {
        "instance_id": 11,
        "recommended_strategy": "Greedy",
        "justification": "Small instance with 10 cities, but Greedy is recommended due to its speed and acceptable 
solution quality for this instance."
    },
    {
        "ins

[Step 1: Duration 93.99 seconds| Input tokens: 121,467 | Output tokens: 3,310]

...

Code execution failed at line 'from smolagents.local_python_executor import ExampleClass' due to: InterpreterError:
Import from smolagents.local_python_executor is not allowed. Authorized imports are: ['collections', 'time', 
'queue', 're', 'random', 'math', 'statistics', 'datetime', 'stat', 'itertools', 'unicodedata'\]

[Step 9: Duration 10.93 seconds| Input tokens: 126,250 | Output tokens: 6,794]

━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ Step 10 ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

[Step 10: Duration 9.68 seconds| Input tokens: 126,886 | Output tokens: 7,266]

KeyboardInterrupt: 